In [1]:
import numpy as np
import tensorflow as tf
from tensorflow.keras.preprocessing.image import ImageDataGenerator
from tensorflow.keras.applications import MobileNetV2
from tensorflow.keras.layers import Dense, GlobalAveragePooling2D
from tensorflow.keras.models import Model
from tensorflow.keras.optimizers import Adam

2025-07-05 11:54:27.953513: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:467] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1751709268.352851    5600 cuda_dnn.cc:8579] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1751709268.472456    5600 cuda_blas.cc:1407] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
W0000 00:00:1751709269.471769    5600 computation_placer.cc:177] computation placer already registered. Please check linkage and avoid linking the same target more than once.
W0000 00:00:1751709269.471791    5600 computation_placer.cc:177] computation placer already registered. Please check linkage and avoid linking the same target more than once.
W0000 00:00:1751709269.471792    5600 computation_placer.cc:177] computation placer alr

In [7]:
base_model = MobileNetV2(weights='imagenet', include_top=False, input_shape=(112, 112, 3))
# Load MobileNetV2 without pre-trained weights
#base_model = MobileNetV2(weights=None, include_top=False, input_shape=(224, 224, 3))

/tmp/ipykernel_89849/498254160.py:1: UserWarning: `input_shape` is undefined or non-square, or `rows` is not in [96, 128, 160, 192, 224]. Weights for input shape (224, 224) will be loaded as the default.
  base_model = MobileNetV2(weights='imagenet', include_top=False, input_shape=(112, 112, 3))


In [8]:
# Add custom layers
x = base_model.output
x = GlobalAveragePooling2D()(x)
x = Dense(1, activation='sigmoid')(x)  # Sigmoid activation for binary classification

model = Model(inputs=base_model.input, outputs=x)

In [9]:
# Freeze the Base Model Layers
for layer in base_model.layers:
    layer.trainable = False

In [10]:
model.compile(optimizer=Adam(), loss='binary_crossentropy', metrics=['accuracy'])

In [11]:
# prepare the data
#train_datagen = ImageDataGenerator(rescale=1./255, validation_split=0.2)

train_datagen = ImageDataGenerator(
    rescale=1./255,
    validation_split=0.2,
    rotation_range=20,
    width_shift_range=0.2,
    height_shift_range=0.2,
    shear_range=0.2,
    zoom_range=0.2,
    horizontal_flip=True,
    fill_mode='nearest',
    brightness_range=(0.8, 1.2)  # Adjust brightness
)

train_generator = train_datagen.flow_from_directory(
    '/home/pico/code/human_presence_classifier/data/human_dataset',
    target_size=(112, 112),
    batch_size=256,
    class_mode='binary',
    subset='training'
)

validation_generator = train_datagen.flow_from_directory(
    '/home/pico/code/human_presence_classifier/data/human_dataset',
    target_size=(112, 112),
    batch_size=256,
    class_mode='binary',
    subset='validation'
)

Found 33280 images belonging to 2 classes.
Found 8320 images belonging to 2 classes.


In [13]:
# Train the model
model.fit(
    train_generator,
    steps_per_epoch=train_generator.samples // train_generator.batch_size,
    validation_data=validation_generator,
    validation_steps=validation_generator.samples // validation_generator.batch_size,
    epochs=3  # Adjust the number of epochs as needed
)

Epoch 1/3
130/130 ━━━━━━━━━━━━━━━━━━━━ 0s 650ms/step - accuracy: 0.7166 - loss: 0.5745

/home/pico/miniconda3/envs/torch/lib/python3.12/site-packages/keras/src/trainers/data_adapters/py_dataset_adapter.py:121: UserWarning: Your `PyDataset` class should call `super().__init__(**kwargs)` in its constructor. `**kwargs` can include `workers`, `use_multiprocessing`, `max_queue_size`. Do not pass these arguments to `fit()`, as they will be ignored.
  self._warn_if_super_not_called()


130/130 ━━━━━━━━━━━━━━━━━━━━ 112s 864ms/step - accuracy: 0.7173 - loss: 0.5733 - val_accuracy: 0.8149 - val_loss: 0.4133
Epoch 2/3
130/130 ━━━━━━━━━━━━━━━━━━━━ 109s 841ms/step - accuracy: 0.8792 - loss: 0.2906 - val_accuracy: 0.8241 - val_loss: 0.3909
Epoch 3/3
130/130 ━━━━━━━━━━━━━━━━━━━━ 109s 841ms/step - accuracy: 0.8955 - loss: 0.2553 - val_accuracy: 0.8364 - val_loss: 0.3779


In [17]:
# Fine tuning
for layer in base_model.layers[-20:]:  # Unfreeze the last 20 layers
    layer.trainable = True

model.compile(optimizer=Adam(learning_rate=1e-5), loss='binary_crossentropy', metrics=['accuracy'])

model.fit(
    train_generator,
    steps_per_epoch=train_generator.samples // train_generator.batch_size,
    validation_data=validation_generator,
    validation_steps=validation_generator.samples // validation_generator.batch_size,
    epochs=12  # Adjust as  12
)

Epoch 1/3
130/130 ━━━━━━━━━━━━━━━━━━━━ 119s 863ms/step - accuracy: 0.9238 - loss: 0.1940 - val_accuracy: 0.8556 - val_loss: 0.3724
Epoch 2/3
130/130 ━━━━━━━━━━━━━━━━━━━━ 110s 846ms/step - accuracy: 0.9227 - loss: 0.1932 - val_accuracy: 0.8599 - val_loss: 0.3490
Epoch 3/3
130/130 ━━━━━━━━━━━━━━━━━━━━ 110s 848ms/step - accuracy: 0.9245 - loss: 0.1904 - val_accuracy: 0.8634 - val_loss: 0.3450


In [18]:
# Save the model
#model.save('binary_classifier_model.keras')

## Now using Pytorch

In [2]:
import os
import shutil
import torch
import torchvision.transforms as transforms
import torchvision.datasets as datasets
from torch.utils.data import DataLoader
import torch.nn as nn
import torch.optim as optim
import random
from tqdm import tqdm

# Set the random seed for reproducibility
seed = 42
random.seed(seed)
torch.manual_seed(seed)
if torch.cuda.is_available():
    torch.cuda.manual_seed(seed)
    torch.cuda.manual_seed_all(seed)

In [3]:
model = torch.hub.load('pytorch/vision:v0.10.0', 'squeezenet1_1', pretrained=True)
model.eval()

Using cache found in /home/pico/.cache/torch/hub/pytorch_vision_v0.10.0
/home/pico/miniconda3/envs/torch/lib/python3.12/site-packages/torchvision/models/_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
/home/pico/miniconda3/envs/torch/lib/python3.12/site-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=SqueezeNet1_1_Weights.IMAGENET1K_V1`. You can also use `weights=SqueezeNet1_1_Weights.DEFAULT` to get the most up-to-date weights.
  warnings.warn(msg)


SqueezeNet(
  (features): Sequential(
    (0): Conv2d(3, 64, kernel_size=(3, 3), stride=(2, 2))
    (1): ReLU(inplace=True)
    (2): MaxPool2d(kernel_size=3, stride=2, padding=0, dilation=1, ceil_mode=True)
    (3): Fire(
      (squeeze): Conv2d(64, 16, kernel_size=(1, 1), stride=(1, 1))
      (squeeze_activation): ReLU(inplace=True)
      (expand1x1): Conv2d(16, 64, kernel_size=(1, 1), stride=(1, 1))
      (expand1x1_activation): ReLU(inplace=True)
      (expand3x3): Conv2d(16, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
      (expand3x3_activation): ReLU(inplace=True)
    )
    (4): Fire(
      (squeeze): Conv2d(128, 16, kernel_size=(1, 1), stride=(1, 1))
      (squeeze_activation): ReLU(inplace=True)
      (expand1x1): Conv2d(16, 64, kernel_size=(1, 1), stride=(1, 1))
      (expand1x1_activation): ReLU(inplace=True)
      (expand3x3): Conv2d(16, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
      (expand3x3_activation): ReLU(inplace=True)
    )
    (5): MaxPool2d

In [4]:
# Print the original classifier
print("Original Classifier:")
print(model.classifier)

# Modify the classifier for binary classification
model.classifier[1] = nn.Conv2d(512, 2, kernel_size=(1, 1), stride=(1, 1))  # Change to 2 classes
model.num_classes = 2  # Update the number of classes

# Print the modified classifier
print("Modified Classifier:")
print(model.classifier)

Original Classifier:
Sequential(
  (0): Dropout(p=0.5, inplace=False)
  (1): Conv2d(512, 1000, kernel_size=(1, 1), stride=(1, 1))
  (2): ReLU(inplace=True)
  (3): AdaptiveAvgPool2d(output_size=(1, 1))
)
Modified Classifier:
Sequential(
  (0): Dropout(p=0.5, inplace=False)
  (1): Conv2d(512, 2, kernel_size=(1, 1), stride=(1, 1))
  (2): ReLU(inplace=True)
  (3): AdaptiveAvgPool2d(output_size=(1, 1))
)


In [5]:
# Freeze the feature extractor layers
for param in model.parameters():
    param.requires_grad = False

# Only train the classifier layers
for param in model.classifier.parameters():
    param.requires_grad = True

In [6]:
# Move the model to the appropriate device (GPU if available)
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model = model.to(device)

In [7]:
# Define the loss function and optimizer
criterion = nn.CrossEntropyLoss()  # Use CrossEntropyLoss for multi-class
optimizer = optim.Adam(model.parameters(), lr=0.0001)  # Use a lower learning rate for fine-tuning

In [8]:
def train_model(train_folder, validation_folder, batch_size=32, epochs=10):
    # Define data augmentation for training
    train_transforms = transforms.Compose([
        transforms.RandomRotation(40),
        transforms.RandomResizedCrop(96),  # SqueezeNet expects 224x224 input
        transforms.RandomHorizontalFlip(),
        transforms.ColorJitter(brightness=0.2),  # Adjust brightness
        transforms.ToTensor(),
        transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])  # Normalize for pre-trained models
    ])

    # Define transformations for validation (no augmentation)
    validation_transforms = transforms.Compose([
        transforms.Resize(256),
        transforms.CenterCrop(96),  # SqueezeNet expects 224x224 input
        transforms.ToTensor(),
        transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])  # Normalize for pre-trained models
    ])

    # Load datasets
    train_dataset = datasets.ImageFolder(root=train_folder, transform=train_transforms)
    validation_dataset = datasets.ImageFolder(root=validation_folder, transform=validation_transforms)

    train_loader = DataLoader(train_dataset, batch_size=batch_size, shuffle=True)
    validation_loader = DataLoader(validation_dataset, batch_size=batch_size, shuffle=False)

    # Training loop
    for epoch in range(epochs):
        model.train()
        running_loss = 0.0
        # Wrap the training loop with tqdm
        with tqdm(total=len(train_loader), desc=f'Epoch {epoch+1}/{epochs}', unit='batch') as pbar:
            for images, labels in train_loader:
                images, labels = images.to(device), labels.to(device)
                optimizer.zero_grad()
                outputs = model(images)
                loss = criterion(outputs, labels)  # Use labels directly for CrossEntropyLoss
                loss.backward()
                optimizer.step()
                running_loss += loss.item()
                
                # Update the progress bar
                pbar.set_postfix(loss=running_loss / (pbar.n + 1))
                pbar.update(1)

        print(f'Epoch [{epoch+1}/{epochs}], Loss: {running_loss/len(train_loader):.4f}')

        # Validation loop
        model.eval()
        with torch.no_grad():
            val_loss = 0.0
            correct = 0
            total = 0
            # Wrap the validation loop with tqdm
            with tqdm(total=len(validation_loader), desc='Validation', unit='batch') as pbar:
                for images, labels in validation_loader:
                    images, labels = images.to(device), labels.to(device)
                    outputs = model(images)
                    loss = criterion(outputs, labels)
                    val_loss += loss.item()
                    _, predicted = torch.max(outputs.data, 1)  # Get the predicted class
                    total += labels.size(0)
                    correct += (predicted == labels).sum().item()
                    
                    # Update the progress bar
                    pbar.update(1)

            print(f'Validation Loss: {val_loss/len(validation_loader):.4f}, Accuracy: {100 * correct / total:.2f}%')

In [9]:
train_folder = '/home/pico/code/human_presence_classifier/data/human_dataset/train'
validation_folder = '/home/pico/code/human_presence_classifier/data/human_dataset/validation'

# Train the model with only the classifier layers
train_model(train_folder, validation_folder, batch_size=32, epochs=5)

# Now, unfreeze the entire model (or specific layers) for fine-tuning
for param in model.parameters():
    param.requires_grad = True  # Unfreeze all layers

# Optionally, you can choose to unfreeze only the last few layers
# for param in model.classifier[-2:].parameters():  # Unfreeze the last two layers of the classifier
#     param.requires_grad = True

# Define a new optimizer for the entire model
optimizer = optim.Adam(model.parameters(), lr=0.00001)  # Use a lower learning rate for fine-tuning

# Continue training the model with fine-tuning
fine_tune_epochs = 3  # Number of epochs for fine-tuning
train_model(train_folder, validation_folder, batch_size=128, epochs=fine_tune_epochs)

Epoch 1/5: 100%|██████████| 1040/1040 [01:01<00:00, 17.01batch/s, loss=0.512]


Epoch [1/5], Loss: 0.5115


Validation: 100%|██████████| 260/260 [00:15<00:00, 16.48batch/s]


Validation Loss: 0.3567, Accuracy: 84.99%


Epoch 2/5: 100%|██████████| 1040/1040 [01:01<00:00, 16.88batch/s, loss=0.404]


...

Validation Loss: 0.3028, Accuracy: 87.43%


Epoch 3/3: 100%|██████████| 260/260 [01:03<00:00,  4.09batch/s, loss=0.311]


Epoch [3/3], Loss: 0.3107


Validation: 100%|██████████| 65/65 [00:15<00:00,  4.20batch/s]

Validation Loss: 0.3017, Accuracy: 87.38%


In [3]:
# Saving the Entire Model
#torch.save(model, 'pytorch_model_9.pth')

# Load the entire model
#model = torch.load('pytorch_model_96.pth')
#loaded_model.eval()  # Set the model to evaluation mode if needed

In [13]:
# Save the model's state dictionary
torch.save(model.state_dict(), 'pytorch_model_9_state_dict.pth')


In [ ]:
# Define the model architecture (must match the original model)
class SimpleModel(nn.Module):
    def __init__(self):
        super(SimpleModel, self).__init__()
        self.fc = nn.Linear(10, 2)  # Example architecture

    def forward(self, x):
        return self.fc(x)

# Instantiate the model
#loaded_model = SimpleModel()

# Load the state dictionary
#loaded_model.load_state_dict(torch.load('model_state_dict.pth'))
#loaded_model.eval()  # Set the model to evaluation mode if needed

In [4]:
model.eval()

SqueezeNet(
  (features): Sequential(
    (0): Conv2d(3, 64, kernel_size=(3, 3), stride=(2, 2))
    (1): ReLU(inplace=True)
    (2): MaxPool2d(kernel_size=3, stride=2, padding=0, dilation=1, ceil_mode=True)
    (3): Fire(
      (squeeze): Conv2d(64, 16, kernel_size=(1, 1), stride=(1, 1))
      (squeeze_activation): ReLU(inplace=True)
      (expand1x1): Conv2d(16, 64, kernel_size=(1, 1), stride=(1, 1))
      (expand1x1_activation): ReLU(inplace=True)
      (expand3x3): Conv2d(16, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
      (expand3x3_activation): ReLU(inplace=True)
    )
    (4): Fire(
      (squeeze): Conv2d(128, 16, kernel_size=(1, 1), stride=(1, 1))
      (squeeze_activation): ReLU(inplace=True)
      (expand1x1): Conv2d(16, 64, kernel_size=(1, 1), stride=(1, 1))
      (expand1x1_activation): ReLU(inplace=True)
      (expand3x3): Conv2d(16, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
      (expand3x3_activation): ReLU(inplace=True)
    )
    (5): MaxPool2d

In [13]:
import torch.onnx

In [17]:
p_model = model.to("cpu")
next(model.parameters()).is_cuda

False

## Convert pytorch model to tensorflow

In [20]:

# Create a dummy input tensor
dummy_input = torch.randn(1,3, 96, 96)  # Batch size of 1,

# Export the model to ONNX format
onnx_file_path = "simple_model.onnx"
torch.onnx.export(p_model, dummy_input, onnx_file_path, 
                  input_names=['input'], output_names=['output'], 
                  dynamic_axes={'input': {0: 'batch_size'}, 'output': {0: 'batch_size'}})

print(f"Model exported to ONNX format at: {onnx_file_path}")

Model exported to ONNX format at: simple_model.onnx


In [25]:
#!pip install onnx onnx-tf
#!pip install onnx2keras

In [26]:
import onnx
from onnx2keras import onnx_to_keras

# Load the ONNX model
onnx_model = onnx.load("/home/pico/code/human_presence_classifier/simple_model.onnx")

k_model = onnx_to_keras(onnx_model, ['squeezenet'])


INFO:onnx2keras:Converter is called.
DEBUG:onnx2keras:List input shapes:
DEBUG:onnx2keras:None
DEBUG:onnx2keras:List inputs:
DEBUG:onnx2keras:Input 0 -> input.
DEBUG:onnx2keras:List outputs:
DEBUG:onnx2keras:Output 0 -> output.
DEBUG:onnx2keras:Gathering weights to dictionary.
DEBUG:onnx2keras:Found weight features.0.weight with shape (64, 3, 3, 3).
DEBUG:onnx2keras:Found weight features.0.bias with shape (64,).
DEBUG:onnx2keras:Found weight features.3.squeeze.weight with shape (16, 64, 1, 1).
DEBUG:onnx2keras:Found weight features.3.squeeze.bias with shape (16,).
DEBUG:onnx2keras:Found weight features.3.expand1x1.weight with shape (64, 16, 1, 1).
DEBUG:onnx2keras:Found weight features.3.expand1x1.bias with shape (64,).
DEBUG:onnx2keras:Found weight features.3.expand3x3.weight with shape (64, 16, 3, 3).
DEBUG:onnx2keras:Found weight features.3.expand3x3.bias with shape (64,).
DEBUG:onnx2keras:Found weight features.4.squeeze.weight with shape (16, 128, 1, 1).
DEBUG:onnx2keras:Found weig

AttributeError: Current node is not in weights / model inputs / layers.

### Extra functions

In [15]:
import os
import numpy as np
import tensorflow as tf
from tensorflow.keras.preprocessing import image
from tensorflow.keras.models import load_model
import shutil

def classify_and_move_images(source_folder, target_folder, model_path, target_class_label=1):
    # Load the trained model
    model = load_model(model_path)

    # Create the target folder if it doesn't exist
    os.makedirs(target_folder, exist_ok=True)

    # List all files in the source folder
    all_files = [f for f in os.listdir(source_folder) if os.path.isfile(os.path.join(source_folder, f))]
    
    # Filter for image files
    image_extensions = ('.jpg', '.jpeg', '.png', '.gif', '.bmp')
    image_files = [f for f in all_files if f.lower().endswith(image_extensions)]
    
    for img_file in image_files:
        img_path = os.path.join(source_folder, img_file)
        
        # Load and preprocess the image
        img = image.load_img(img_path, target_size=(224, 224))  # Resize to match model input
        img_array = image.img_to_array(img)
        img_array = np.expand_dims(img_array, axis=0)  # Add batch dimension
        img_array /= 255.0  # Rescale pixel values

        # Make predictions
        predictions = model.predict(img_array)
        predicted_class = 1 if predictions[0] > 0.6 else 0  # Assuming binary classification

        # Move the image if it belongs to the target class
        if predicted_class == target_class_label:
            shutil.move(img_path, os.path.join(target_folder, img_file))
            print(f'Moved: {img_file} to {target_folder}')

# Example usage
#classify_and_move_images('/home/pico/code/human_presence_classifier/data/human', '/home/pico/code/human_presence_classifier/data/no_human',
#                          '/home/pico/code/human_presence_classifier/binary_classifier_model.keras', target_class_label=0)

1/1 ━━━━━━━━━━━━━━━━━━━━ 2s 2s/step
Moved: 000000569341.jpg to /home/pico/code/human_presence_classifier/data/no_human
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step
Moved: 000000246270.jpg to /home/pico/code/human_presence_classifier/data/no_human
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step
Moved: 000000349841.jpg to /home/pico/code/human_presence_classifier/data/no_human
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step
Moved: 000000095161.jpg to /home/pico/code/human_presence_classifier/data/no_human
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step
Moved: 000000393900.jpg to /home/pico/code/human_presence_classifier/data/no_human
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 28ms/step
Moved: 000000160542.jpg to /home/pico/code/human_presence_classifier/data/no_human
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step
Moved: 000000073527.jpg to /home/pico/code/human_presence_classifier/data/no_human
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 28ms/step
Moved: 000000323427.jpg to /home/pico/code/human_presence_classifier/data/no_human
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/s

KeyboardInterrupt: 

In [2]:
import os
import shutil

def move_images(source_folder, destination_folder, n):
    # Create the destination folder if it doesn't exist
    if not os.path.exists(destination_folder):
        os.makedirs(destination_folder)

    # Get a list of all image files in the source folder
    image_files = [f for f in os.listdir(source_folder) if f.lower().endswith(('.png', '.jpg', '.jpeg', '.gif', '.bmp'))]

    # Move the specified number of images
    for image in image_files[:n]:
        source_path = os.path.join(source_folder, image)
        destination_path = os.path.join(destination_folder, image)
        shutil.move(source_path, destination_path)
        print(f'Moved: {image}')

# Example usage
source = '/home/pico/code/human_presence_classifier/data/no_human'
destination = '/home/pico/code/human_presence_classifier/data/no_human1'
number_of_images = 10400

#move_images(source, destination, number_of_images)

In [2]:
import os
import random
import shutil

def move_random_images(source_folder, target_folder_name='selected_images'):
    # Get the parent directory of the source folder
    parent_directory = os.path.dirname(source_folder)
    
    # Create the target folder path at the same level as the source folder
    target_folder = os.path.join(parent_directory, target_folder_name)
    
    # Create the target folder if it doesn't exist
    os.makedirs(target_folder, exist_ok=True)
    
    # List all files in the source folder
    all_files = [f for f in os.listdir(source_folder) if os.path.isfile(os.path.join(source_folder, f))]
    
    # Filter for image files (you can add more extensions if needed)
    image_extensions = ('.jpg', '.jpeg', '.png', '.gif', '.bmp')
    image_files = [f for f in all_files if f.lower().endswith(image_extensions)]
    
    # Calculate the number of images to move (20%)
    num_images_to_move = int(len(image_files) * 0.2)
    
    # Randomly select images
    selected_images = random.sample(image_files, num_images_to_move)
    
    # Move selected images to the target folder
    for image in selected_images:
        shutil.move(os.path.join(source_folder, image), os.path.join(target_folder, image))
    
    print(f'Moved {num_images_to_move} images to {target_folder}')

# Example usage
#move_random_images('/home/pico/code/human_presence_classifier/data/human_dataset/no_human_train', 'no_human_validation')

Moved 4160 images to /home/pico/code/human_presence_classifier/data/human_dataset/no_human_validation
